In [62]:
import pandas as pd


# 读取数据
def read_data():
    df_land = pd.read_excel('./data/1.xlsx', sheet_name=0)
    df_crop_land = pd.read_excel('./data/1.xlsx', sheet_name=1)
    df_planting = pd.read_excel('./data/2.xlsx', sheet_name=0)
    df_crop_details = pd.read_excel('./data/2.xlsx', sheet_name=1)
    return df_land, df_crop_land, df_planting, df_crop_details


# 数据预处理
def preprocess_data(df_land, df_crop_land, df_planting, df_crop_details):
    # 合并地块信息和种植信息
    df_merged = pd.merge(df_land, df_planting, left_on='地块名称', right_on='种植地块')

    # 合并作物信息和地块类型信息
    df_crop_details['销售单价中间值'] = df_crop_details['销售单价/(元/斤)'].apply(
        lambda x: (x.split('-')[0] + x.split('-')[1]) / 2)
    df_final = pd.merge(df_merged, df_crop_details, on=['作物编号', '作物名称', '地块类型', '种植季次'])

    return df_final


# 计算总产量和总销售收入
def calculate_stats(df_final):
    df_final['总产量'] = df_final['亩产量/斤'] * df_final['种植面积/亩']
    df_final['总销售收入'] = df_final['总产量'] * df_final['销售单价中间值']

    # 按地块类型和作物名称分组统计
    df_grouped = df_final.groupby(['地块类型', '作物名称']).agg({'总产量': 'sum', '总销售收入': 'sum'}).reset_index()

    # 按作物名称统计
    df_crop_stats = df_final.groupby('作物名称').agg({'总产量': 'sum', '总销售收入': 'sum'}).reset_index()

    return df_grouped, df_crop_stats


df_land, df_crop_land, df_planting, df_crop_details = read_data()
print(read_data())

(   landName landType  landArea
0        A1      平旱地      80.0
1        A2      平旱地      55.0
2        A3      平旱地      35.0
3        A4      平旱地      72.0
4        A5      平旱地      68.0
5        A6      平旱地      55.0
6        B1       梯田      60.0
7        B2       梯田      46.0
8        B3       梯田      40.0
9        B4       梯田      28.0
10       B5       梯田      25.0
11       B6       梯田      86.0
12       B7       梯田      55.0
13       B8       梯田      44.0
14       B9       梯田      50.0
15      B10       梯田      25.0
16      B11       梯田      60.0
17      B12       梯田      45.0
18      B13       梯田      35.0
19      B14       梯田      20.0
20       C1      山坡地      15.0
21       C2      山坡地      13.0
22       C3      山坡地      15.0
23       C4      山坡地      18.0
24       C5      山坡地      27.0
25       C6      山坡地      20.0
26       D1      水浇地      15.0
27       D2      水浇地      10.0
28       D3      水浇地      14.0
29       D4      水浇地       6.0
30       D5      水浇地      10.0
31     

In [63]:
df_final = preprocess_data(df_land, df_crop_land, df_planting, df_crop_details)
df_grouped, df_crop_stats = calculate_stats(df_final)

print("按地块类型和作物名称统计的总产量和总销售收入:")
print(df_grouped)
print("\n按作物名称统计的总产量和总销售收入:")
print(df_crop_stats)

KeyError: '种植地块'

In [81]:
import enum


# class LandType(enum.Enum):
#     # A = 0
#     # B = 1
#     # C = 2
#     # D = 3
#     # E = 4
#     # F = 5
#     A = "平旱地"
#     B = "梯田"
#     C = "山坡地"
#     D = "水浇地"
#     E = "普通大棚"
#     F = "智慧大棚"

LandType = {"A": "平旱地", "B": "梯田", "C": "山坡地", "D": "水浇地", "E": "普通大棚", "F": "智慧大棚"}

class Land:
    landName = ""
    landType = ""
    landArea = 0

    def __init__(self, land_name, land_type, land_area):
        self.landName = land_name
        self.landType = land_type
        self.landArea = land_area

    def __str__(self):
        return f"地块名称:{self.landName}, 地块类型:{self.landType}, 地块面积:{self.landArea}"

    def __repr__(self):
        return self.__str__()


df_land = pd.read_excel('./data/1.xlsx', sheet_name=0)
land_list = []
for i in range(len(df_land)):
    land_list.append(Land(df_land.loc[i, 'landName'], df_land.loc[i, 'landType'], df_land.loc[i, 'landArea']))


In [82]:
df_planting = pd.read_excel('./data/2.xlsx', sheet_name=0)
df_crop_details = pd.read_excel('./data/2.xlsx', sheet_name=1)

In [83]:
df_crop_details

no  cropNum cropName cropLandType season  unitYield  cost       price
0      1        1       黄豆          平旱地     单季        400   400   2.50-4.00
1      2        2       黑豆          平旱地     单季        500   400   6.50-8.50
2      3        3       红豆          平旱地     单季        400   350   7.50-9.00
3      4        4       绿豆          平旱地     单季        350   350   6.00-8.00
4      5        5       爬豆          平旱地     单季        415   350   6.00-7.50
..   ...      ...      ...          ...    ...        ...   ...         ...
102  103       30      生菜          智慧大棚    第二季       4500  2200   5.40-7.20
103  104       31       辣椒         智慧大棚    第二季       1800  1300  7.20-10.20
104  105       32      空心菜         智慧大棚    第二季      11000  5500   3.60-7.20
105  106       33      黄心菜         智慧大棚    第二季       5400  2750   4.80-6.00
106  107       34       芹菜         智慧大棚    第二季       6000  1200   3.80-5.80

[107 rows x 8 columns]

In [84]:
df_planting

landName  cropNum cropName cropType  plantArea season
0        A1        6       小麦       粮食       80.0     单季
1        A2        7       玉米       粮食       55.0     单季
2        A3        7       玉米       粮食       35.0     单季
3        A4        1       黄豆   粮食（豆类）       72.0     单季
4        A5        4       绿豆   粮食（豆类）       68.0     单季
..      ...      ...      ...      ...        ...    ...
82      NaN       28      小青菜      蔬菜         0.3    第二季
83      NaN       30      生菜       蔬菜         0.3    第二季
84       F4       19       芸豆   蔬菜（豆类）        0.6    第一季
85      NaN       34       芹菜      蔬菜         0.3    第二季
86      NaN       23      菠菜       蔬菜         0.3    第二季

[87 rows x 6 columns]

In [85]:
# 定义过滤条件
condition = (df_crop_details['cropNum'] == 8) & (df_crop_details['cropLandType'] == '平旱地') & (
            df_crop_details['season'] == '单季')

# 应用过滤条件
filtered_df = df_crop_details[condition]
filtered_df.cost

7    360
Name: cost, dtype: int64

In [103]:
def get_crop_price(crop_num, crop_land_type, season):
    if crop_land_type=="智慧大棚" and season=="第一季":
        crop_land_type = "普通大棚"
    s =  df_crop_details[(df_crop_details['cropNum'] == crop_num) & (df_crop_details['cropLandType'] == crop_land_type) & (
            df_crop_details['season'] == season)].price.values[0].split('-')
    return (float(s[0]) + float(s[1])) / 2

def get_crop_yield(crop_num, crop_land_type, season):
    if crop_land_type=="智慧大棚" and season=="第一季":
        crop_land_type = "普通大棚"
    return df_crop_details[(df_crop_details['cropNum'] == crop_num) & (df_crop_details['cropLandType'] == crop_land_type) & (
            df_crop_details['season'] == season)].unitYield.values[0]

def get_crop_cost(crop_num, crop_land_type, season):
    if crop_land_type=="智慧大棚" and season=="第一季":
        crop_land_type = "普通大棚"
    return df_crop_details[(df_crop_details['cropNum'] == crop_num) & (df_crop_details['cropLandType'] == crop_land_type) & (
            df_crop_details['season'] == season)].cost.values[0]

In [97]:
get_crop_price(8, '平旱地', '单季')

6.75

In [94]:
df_planting['landName'] = df_planting['landName'].ffill()
df_crop_details['cropLandType'] = df_crop_details['cropLandType'].str.rstrip()

In [107]:
total_yield = {crop:0 for crop in df_crop_details['cropNum'].unique()}
total_cost = {crop:0 for crop in df_crop_details['cropNum'].unique()}
total_income = {crop:0 for crop in df_crop_details['cropNum'].unique()}
total_profit = {crop:0 for crop in df_crop_details['cropNum'].unique()}
for line in df_planting.values:
    print(line)
    print(line[1], LandType[line[0][0]], line[5])
    yld = line[4] * get_crop_yield(line[1], LandType[line[0][0]], line[5])
    cost = line[4] * get_crop_cost(line[1], LandType[line[0][0]], line[5])
    income = yld * get_crop_price(line[1], LandType[line[0][0]], line[5])
    profit = income - cost
    
    total_yield[line[1]] += yld
    total_cost[line[1]] += cost
    total_income[line[1]] += income
    total_profit[line[1]] += profit
total_profit

['A1' 6 '小麦' '粮食' 80.0 '单季']
6 平旱地 单季
['A2' 7 '玉米' '粮食' 55.0 '单季']
7 平旱地 单季
['A3' 7 '玉米' '粮食' 35.0 '单季']
7 平旱地 单季
['A4' 1 '黄豆' '粮食（豆类）' 72.0 '单季']
1 平旱地 单季
['A5' 4 '绿豆' '粮食（豆类）' 68.0 '单季']
4 平旱地 单季
['A6' 8 '谷子' '粮食' 55.0 '单季']
8 平旱地 单季
['B1' 6 '小麦' '粮食' 60.0 '单季']
6 梯田 单季
['B2' 2 '黑豆' '粮食（豆类）' 46.0 '单季']
2 梯田 单季
['B3' 3 '红豆' '粮食（豆类）' 40.0 '单季']
3 梯田 单季
['B4' 4 '绿豆' '粮食（豆类）' 28.0 '单季']
4 梯田 单季
['B5' 5 '爬豆' '粮食（豆类）' 25.0 '单季']
5 梯田 单季
['B6' 8 '谷子' '粮食' 86.0 '单季']
8 梯田 单季
['B7' 6 '小麦' '粮食' 55.0 '单季']
6 梯田 单季
['B8' 8 '谷子' '粮食' 44.0 '单季']
8 梯田 单季
['B9' 9 '高粱' '粮食' 50.0 '单季']
9 梯田 单季
['B10' 10 '黍子' '粮食' 25.0 '单季']
10 梯田 单季
['B11' 1 '黄豆' '粮食（豆类）' 60.0 '单季']
1 梯田 单季
['B12' 7 '玉米' '粮食' 45.0 '单季']
7 梯田 单季
['B13' 14 '莜麦' '粮食' 35.0 '单季']
14 梯田 单季
['B14' 15 '大麦' '粮食' 20.0 '单季']
15 梯田 单季
['C1' 11 '荞麦' '粮食' 15.0 '单季']
11 山坡地 单季
['C2' 12 '南瓜' '粮食' 13.0 '单季']
12 山坡地 单季
['C3' 1 '黄豆' '粮食（豆类）' 15.0 '单季']
1 山坡地 单季
['C4' 13 '红薯' '粮食' 18.0 '单季']
13 山坡地 单季
['C5' 6 '小麦' '粮食' 27.0 '单季']
6 山坡地 单季
['C6' 3 '红豆' '粮

{1: 126450.0,
 2: 145475.0,
 3: 163800.0,
 4: 197680.0,
 5: 57906.25,
 6: 498040.0,
 7: 330750.0,
 8: 415350.0,
 9: 160000.0,
 10: 84750.0,
 11: 54750.0,
 12: 39650.0,
 13: 81000.0,
 14: 63000.0,
 15: 28000.0,
 16: 118440.0,
 17: 267520.0,
 18: 168000.0,
 19: 37800.0,
 20: 82500.0,
 21: 197093.0,
 22: 237624.0,
 23: 5310.0,
 24: 13098.0,
 25: 17100.0,
 26: 23175.0,
 27: 20700.0,
 28: 187392.0,
 29: 93765.0,
 30: 15120.000000000002,
 31: 7980.0,
 32: 14700.0,
 33: 7350.0,
 34: 8280.0,
 35: 315000.0,
 36: 237500.0,
 37: 111000.0,
 38: 512100.0,
 39: 133200.0,
 40: 270000.0,
 41: 378000.0}